## Trade Adjustment Assistance for Workers
The [U.S. Department of Labor web site](https://www.dol.gov/general/topic/training/tradeact) gives the following description of the Trade Adjustment Assistance (TAA) Program:

> The [Trade Adjustment Assistance (TAA) Program](https://www.doleta.gov/tradeact/) is a federal program established under the [Trade Adjustment Assistance Reauthorization Act of 2015](https://www.doleta.gov/tradeact/law/) that provides aid to workers who lose their jobs or whose hours of work and wages are reduced as a result of increased imports.

You can search for TAA cases on [this page](https://www.doleta.gov/tradeact/petitioners/taa_search_form.cfm).  The resulting data can then be downloaded into an Excel file for later analysis.  The following Python code shows several examples of how this can be done.

### Group the TAA Petitions by Company and Sort by the Number of Certified Petitions since 2012

The file Location_by_Date_search_d2012.xls is created by going to the [search page](https://www.doleta.gov/tradeact/petitioners/taa_search_form.cfm), entering "1/1/2012" (without the quotes) for the "With determination date from" field, select "All" from the States select list, and hit the "Generate report" button.  The resulting page should display the first 20 of 8334 records found.  Click the "Export All to Excel" button, rename the resulting file to Location_by_Date_search_d2012.xls, and place it in the directory of this Jupyter notebook (taa.ipynb).  The following Python code will then group the TAA petitions by company and sort by the number of certified petitions since 2012:

In [5]:
import pandas as pd
xx = pd.read_html("Location_by_Date_search_d2012.xls", header=0)
tt = xx[0]
tt['Impact_Date'] = pd.to_datetime(tt['Impact date'])
#print(type(tt))
#print(tt.info())
print(tt.shape)
cc = tt.loc[tt['Decision'] == 'Certified']
cc = cc.loc[pd.to_datetime(cc['Impact date']) > pd.to_datetime('1/1/2012')]
#print(cc.shape)
#print(cc.head())
gg = cc.groupby(['Company']).agg({'Decision Date':"count", 'Impact_Date':"max"})
gg = gg.reset_index(level=['Company'])
gg.columns = ['Company','Count','Last Date']
gg = gg.sort_values(by=['Count','Last Date'], ascending=False)
print(gg.head(50))


(8334, 11)
                                                Company  Count  Last Date
2255                                  Quest Diagnostics     45 2014-01-01
1420  International Business Machines Corporation (IBM)     42 2016-05-11
2558                         Southern California Edison     30 2016-05-03
418                                 Boyd Coffee Company     29 2016-10-27
2778                              The McClatchy Company     29 2015-04-27
973                                            Experian     23 2016-09-13
470                                      CDM Smith Inc.     22 2016-09-13
1595                                    LSI Corporation     20 2015-03-14
2548                             Sony Electronics, Inc.     19 2014-06-21
1289                         Hewlett Packard Enterprise     17 2017-04-12
1351                                    IBM Corporation     17 2013-01-15
2903                    United States Steel Corporation     15 2017-03-13
1862                       

As can be seen, the top three companies by number of certified petitions since 2012 are Quest Diagnostics, International Business Machines Corporation (IBM), and Southern California Edison.  The "Last Date" column lists the latest "Impact date" of all of the petitions.  Note that there appears to be duplicate companies.  For example, the above output lists the following three lines, all for IBM:

1. 1420  International Business Machines Corporation (IBM)     42 2016-05-11
2. 1351                                    IBM Corporation     17 2013-01-15
3. 1418              International Business Machines (IBM)      7 2016-09-25

The problem is that these are three different spellings for the company.

### Group the TAA Petitions by Company and Location and Sort by the Number of Certified Petitions since 2012
The following Python code will do the same thing as the prior code except that it will group by the Company-Location combination, not just by the Company.


In [6]:
import pandas as pd
xx = pd.read_html("Location_by_Date_search_d2012.xls", header=0)
tt = xx[0]
tt['Impact_Date'] = pd.to_datetime(tt['Impact date'])
print(tt.shape)
cc = tt.loc[tt['Decision'] == 'Certified']
cc = cc.loc[pd.to_datetime(cc['Impact date']) > pd.to_datetime('1/1/2012')]
gg = cc.groupby(['Company','Location']).agg({'Decision Date':"count", 'Impact_Date':"max"})
gg = gg.reset_index(level=['Company','Location'])
gg.columns = ['Company','Location','Count','Last Date']
gg = gg.sort_values(by=['Count','Last Date'], ascending=False)
print(gg.head(50).to_string(index=''))


(8334, 11)
Company              Location  Count  Last Date
                Halliburton Energy Services, Inc.            Duncan, OK      6 2015-08-02
                            Bush Industries, Inc.         Jamestown, NY      5 2017-11-14
International Business Machines Corporation (IBM)            Armonk, NY      5 2015-12-08
                                  AVX Corporation      Myrtle Beach, SC      4 2018-03-04
                            Lufkin Industries LLC            Lufkin, TX      4 2017-05-02
                                  Thomson Reuters          New York, NY      4 2017-04-18
International Business Machines Corporation (IBM)      Poughkeepsie, NY      4 2016-03-01
International Business Machines Corporation (IBM)           Boulder, CO      4 2015-08-23
                          Maersk Agency USA, Inc.         Charlotte, NC      4 2015-03-25
                         Remy USA Industries, LLC         Bay Shore, NY      4 2013-08-15
                                  IBM Cor

As can be seen, a number of companies have multiple certified petitions from multiple locations.  For example, IBM has multiple petitions for Armonk NY, Poughkeepsie NY, Boulder CO, Essex Junction VT, Austin TX, and Rochester MN in the list above.

### Group the TAA Petitions by Location for a Specific Company
The following Python code will do the same thing as the prior code except that it will list entries for a single specified company. The first listing (by Company) above shows 30 petitions for Southern California Edison but the next listing (by Company and Location) lists no petitions for that company.  The output from the following code reveals that this is because all of the locations are unique except for 2 petitions for Rosemead, CA.  For that reason, they didn't show up in the second listing which lists all of the companies/locations with 3 or more petitions.

In [7]:
import pandas as pd
xx = pd.read_html("Location_by_Date_search_d2012.xls", header=0)
tt = xx[0]
tt['Impact_Date'] = pd.to_datetime(tt['Impact date'])
print(tt.shape)
cc = tt.loc[tt['Decision'] == 'Certified']
cc = cc.loc[pd.to_datetime(cc['Impact date']) > pd.to_datetime('1/1/2012')]
cc = cc.loc[cc['Company'] == 'Southern California Edison']
gg = cc.groupby(['Company','Location']).agg({'Decision Date':"count", 'Impact_Date':"max"})
gg = gg.reset_index(level=['Company','Location'])
gg.columns = ['Company','Location','Count','Last Date']
gg = gg.sort_values(by=['Count','Last Date'], ascending=False)
print(gg.head(50).to_string(index=''))


(8334, 11)
Company              Location  Count  Last Date
Southern California Edison          Rosemead, CA      2 2016-05-03
Southern California Edison          Alhambra, CA      1 2012-12-18
Southern California Edison       Bakersfield, CA      1 2012-12-18
Southern California Edison         Big Creek, CA      1 2012-12-18
Southern California Edison            Bishop, CA      1 2012-12-18
Southern California Edison      Boulder City, NV      1 2012-12-18
Southern California Edison    Cathedral City, CA      1 2012-12-18
Southern California Edison           Compton, CA      1 2012-12-18
Southern California Edison           Fontana, CA      1 2012-12-18
Southern California Edison         Fullerton, CA      1 2012-12-18
Southern California Edison          Hesperia, CA      1 2012-12-18
Southern California Edison            Irvine, CA      1 2012-12-18
Southern California Edison         Irwindale, CA      1 2012-12-18
Southern California Edison          La Palma, CA      1 2012-12-18
Sou

### Group the TAA Petitions by Company and Sort by Number of Certified Petitions for a Specified State

The file Location_by_Date_search_MA.xls is created by going to the [search page](https://www.doleta.gov/tradeact/petitioners/taa_search_form.cfm), select the specified state (MA) from the States select list, and hit the "Generate report" button.  The resulting page should display the first 20 of 2459 records found.  Click the "Export All to Excel" button, rename the resulting file to Location_by_Date_search_MA.xls, and place it in the directory of this Jupyter notebook (taa.ipynb).  The following Python code will then group the TAA petitions by company and sort by the number of certified petitions since 2012:


In [8]:
import pandas as pd
xx = pd.read_html("Location_by_Date_search_MA.xls", header=0)
tt = xx[0]
tt['Impact_Date'] = pd.to_datetime(tt['Impact date'])
print(tt.shape)
cc = tt.loc[tt['Decision'] == 'Certified']
cc = cc.loc[pd.to_datetime(cc['Impact date']) > pd.to_datetime('1/1/2012')]
gg = cc.groupby(['Company']).agg({'Decision Date':"count", 'Impact_Date':"max"})
gg = gg.reset_index(level=['Company'])
gg.columns = ['Company','Count','Last Date']
gg = gg.sort_values(by=['Count','Last Date'], ascending=False)
print(gg.head(50))


(2459, 11)
                                               Company  Count  Last Date
127                                      Staples, Inc.      3 2017-01-25
49                                     EMC Corporation      3 2015-07-05
122                                    SimplexGrinnell      2 2017-05-17
70                          Hewlett Packard Enterprise      2 2017-04-12
131                         Stratus Technologies, Inc.      2 2016-06-08
76   International Business Machines Corporation (IBM)      2 2016-05-11
23                                    Bose Corporation      2 2016-01-26
129                           State Street Corporation      2 2015-10-17
34                                   Citizens Bank, NA      2 2015-10-01
66                             Haemonetics Corporation      2 2015-06-07
100                              Microsemi Corporation      2 2014-08-31
105                                     Osram Sylvania      2 2013-12-10
39                                      

Note: The Jupyter Notebook from which this post is generated can be found at http://econdataus.com/taa1.ipynb.